In [ ]:
import nest_asyncio
import websockets
import json
import uuid
import json
import uuid
import base64
import wave
import soundfile as sf
import numpy as np
from IPython.display import Audio, display

nest_asyncio.apply()

API_KEY = ""


async def test_connection():
    url = "wss://api.openai.com/v1/realtime?model=gpt-4o-realtime-preview-2024-10-01"
    headers = {
        "Authorization": f"Bearer {API_KEY}",
        "OpenAI-Beta": "realtime=v1"
    }

    async with websockets.connect(url, additional_headers=headers) as websocket:
        print("✅ Connected to OpenAI Realtime API")

# Run the async function
asyncio.run(test_connection())


✅ Connected to OpenAI Realtime API


In [ ]:
# @title Helper Code to Generate Conversation
import asyncio
import websockets
import json
import uuid
import base64
import io
import wave
from IPython.display import Audio, display

async def text_to_speech_realtime(text: str, output_path: str = "response.wav", api_key=API_KEY):
    url = "wss://api.openai.com/v1/realtime?model=gpt-4o-realtime-preview-2024-10-01"
    headers = {
        "Authorization": f"Bearer {api_key}",
        "OpenAI-Beta": "realtime=v1"
    }

    audio_chunks = []

    async with websockets.connect(url, additional_headers=headers) as ws:
        # Wait for the session to be created
        await ws.recv()

        # Set the system prompt to repeat user input verbatim
        await ws.send(json.dumps({
            "type": "session.update",
            "session": {
                "instructions": f"REPEAT WHAT I SAID HERE: {text}"
            }
        }))

        # Send the user's message
        await ws.send(json.dumps({
            "type": "conversation.item.create",
            "event_id": str(uuid.uuid4()),
            "item": {
                "type": "message",
                "text": text
            }
        }))

        # Request the model's response
        await ws.send(json.dumps({
            "type": "response.create",
            "event_id": str(uuid.uuid4())
        }))

        # Collect the audio response
        while True:
            response = await ws.recv()
            data = json.loads(response)
            if data.get("type") == "response.audio.delta":
                delta = data.get("delta")
                if delta:
                    audio_chunks.append(base64.b64decode(delta))
            if data.get("type") == "response.done":
                break

    # Save and play the audio
    if audio_chunks:
        audio_bytes = b"".join(audio_chunks)
        wav_io = io.BytesIO()
        with wave.open(wav_io, 'wb') as wav_file:
            wav_file.setnchannels(1)
            wav_file.setsampwidth(2)
            wav_file.setframerate(24000)
            wav_file.writeframes(audio_bytes)

        with open(output_path, "wb") as f:
            f.write(wav_io.getvalue())

        wav_io.seek(0)
        display(Audio(wav_io.read(), rate=24000))
        print(f"✅ Saved: {output_path}")

import asyncio

async def generate_user_audio_inputs(user_texts):
    """
    Converts a list of user text inputs to audio files.
    :param user_texts: List of strings representing user inputs.
    :param api_key: Your OpenAI API key.
    :return: List of filenames of the generated audio files.
    """
    audio_files = []
    for idx, text in enumerate(user_texts):
        filename = f"user_input_{idx + 1}.wav"
        await text_to_speech_realtime(text, output_path=filename)
        audio_files.append(filename)
    return audio_files


In [ ]:
user_texts = [
    "Hello, how are you?",
    "Let me stop you right there Can you tell me a joke?",
    "That's interesting, tell me more.",
    "Ahh thats awesome haha"
]


audio_files = asyncio.run(generate_user_audio_inputs(user_texts))


✅ Saved: user_input_1.wav


✅ Saved: user_input_2.wav


✅ Saved: user_input_3.wav


✅ Saved: user_input_4.wav


In [ ]:

async def run_single_turn_conversation(
    user_wav="user_input.wav",
    assistant_wav="assistant_response.wav",
    conversation_wav="conversation.wav"
):
    """
    Streams a pre-recorded user WAV to OpenAI Realtime API, collects the assistant's
    reply (in a different voice), then concatenates user + pause + assistant into one WAV.
    """

    # 2. Connect to the Realtime WebSocket, specifying GPT-4o Realtime
    url = "wss://api.openai.com/v1/realtime?model=gpt-4o-realtime-preview-2024-10-01"
    headers = {
        "Authorization": f"Bearer {API_KEY}",
        "OpenAI-Beta": "realtime=v1"
    }

    async with websockets.connect(url, additional_headers=headers) as ws:
        # 3. Wait for session.created acknowledgment
        init_evt = await ws.recv()
        print("Received:", init_evt)  # e.g., {"type":"session.created", ...}

        # 4. Send session.update, including "voice": "ash"
        sess_update = {
            "type": "session.update",
            "session": {
                "voice": "ash",                    # ← CHANGE: assistant speaks in "ash" voice
                "input_audio_format": "pcm16",     # 16-bit PCM @ 24 kHz mono
                "output_audio_format": "pcm16",    # request PCM16 reply
                "turn_detection": {
                    "type": "server_vad",          # server will detect end-of-speech
                    "create_response": False       # do not auto-generate until we call response.create
                }
            }
        }
        await ws.send(json.dumps(sess_update))
        upd_resp = await ws.recv()
        print("Received:", upd_resp)  # e.g., {"type":"session.updated", ...}

        # 5. Read & encode the user WAV file (must be 24 kHz mono PCM16)
        data, sr = sf.read(user_wav, dtype="int16")
        assert sr == 24000 and data.ndim == 1, "WAV must be 24 kHz mono, 16-bit PCM"
        pcm_bytes = data.tobytes()
        b64_audio = base64.b64encode(pcm_bytes).decode("utf-8")

        # 6. Append the entire user audio buffer under "audio"
        append_msg = {
            "type": "input_audio_buffer.append",
            "audio": b64_audio
        }
        await ws.send(json.dumps(append_msg))

        # 7. Commit buffer as a single user turn
        commit_msg = {
            "type": "input_audio_buffer.commit"
        }
        await ws.send(json.dumps(commit_msg))

        # 8. Wait for "input_audio_buffer.committed" & "conversation.item.created"
        while True:
            evt = await ws.recv()
            evt_obj = json.loads(evt)
            print("Received:", evt_obj)
            if evt_obj.get("type") == "input_audio_buffer.committed":
                continue  # buffer is now committed; keep listening
            if evt_obj.get("type") == "conversation.item.created":
                break     # user turn was registered successfully

        # 9. Explicitly request the assistant’s audio response
        resp_create = {
            "type": "response.create"
        }
        await ws.send(json.dumps(resp_create))

        # 10. Collect assistant audio deltas (base64 PCM16), decode & accumulate
        collected_pcm = bytearray()
        while True:
            resp_evt = await ws.recv()
            resp_obj = json.loads(resp_evt)

            if resp_obj.get("type") == "response.audio.delta":
                delta_b64 = resp_obj.get("delta", "")
                if delta_b64:
                    collected_pcm.extend(base64.b64decode(delta_b64))

            if resp_obj.get("type") == "response.done":
                print("Received:", resp_obj)  # {"type":"response.done"}
                break

        # 11. Write the assistant’s audio to a WAV file (PCM16 @ 24 kHz mono)
        if collected_pcm:
            with wave.open(assistant_wav, "wb") as wav_out:
                wav_out.setnchannels(1)       # mono
                wav_out.setsampwidth(2)       # 16 bits (2 bytes per sample)
                wav_out.setframerate(24000)   # 24 kHz
                wav_out.writeframes(bytes(collected_pcm))
            print(f"✅ Saved assistant audio to {assistant_wav}")
        else:
            print("⚠️ No assistant audio received.")
            return  # abort concatenation if no assistant audio

        # 12. Concatenate user + 0.5 s pause + assistant into conversation.wav
        # 12.1. Read back both WAVs as int16 arrays
        user_data, _ = sf.read(user_wav, dtype="int16")
        assistant_data, _ = sf.read(assistant_wav, dtype="int16")

        # 12.2. Create 0.5 second (24000 * 0.5 = 12000) of silence (int16 zeros)
        pause_len = int(0.5 * 24000)  # 12,000 samples of silence
        pause = np.zeros(pause_len, dtype="int16")

        # 12.3. Concatenate: user → pause → assistant
        conversation_data = np.concatenate((user_data, pause, assistant_data))
        # 12.4. Write `conversation.wav`
        with wave.open(conversation_wav, "wb") as wav_out:
            wav_out.setnchannels(1)           # mono
            wav_out.setsampwidth(2)           # 16 bits
            wav_out.setframerate(24000)       # 24 kHz
            wav_out.writeframes(conversation_data.tobytes())
        print(f"✅ Saved conversation audio to {conversation_wav}")

        # 13. Play back `conversation.wav` in Colab
        display(Audio(conversation_wav, rate=24000))
asyncio.run(run_single_turn_conversation(
    user_wav="user_input_1.wav",
    assistant_wav="assistant_response.wav",
    conversation_wav="conversation.wav"
))


Received: {"type":"session.created","event_id":"event_Be0ecrhtGuRUXJmAXJzNc","session":{"id":"sess_Be0ecTf94fM2TyJrZo0Or","object":"realtime.session","expires_at":1748877134,"input_audio_noise_reduction":null,"turn_detection":{"type":"server_vad","threshold":0.5,"prefix_padding_ms":300,"silence_duration_ms":200,"create_response":true,"interrupt_response":true},"input_audio_format":"pcm16","input_audio_transcription":null,"client_secret":null,"include":null,"model":"gpt-4o-realtime-preview-2024-10-01","modalities":["text","audio"],"instructions":"Your knowledge cutoff is 2023-10. You are a helpful, witty, and friendly AI. Act like a human, but remember that you aren't a human and that you can't do human things in the real world. Your voice and personality should be warm and engaging, with a lively and playful tone. If interacting in a non-English language, start by using the standard accent or dialect familiar to the user. Talk quickly. You should always call a function if you can. Do n

In [ ]:
async def run_multi_turn_conversation(
    audio_files,
    assistant_voice="coral",
    final_output="multi_turn_conversation.wav"
):
    """
    Simulates a multi-turn conversation over Realtime API with interruption handling.
    Streams each user WAV in `audio_files`, fetches assistant replies in `assistant_voice`,
    demonstrates interruption on the first turn only (after ~3 deltas), and concatenates into final_output WAV.
    """
    url = "wss://api.openai.com/v1/realtime?model=gpt-4o-realtime-preview-2024-10-01"
    headers = {
        "Authorization": f"Bearer {API_KEY}",
        "OpenAI-Beta": "realtime=v1"
    }

    # Buffers to accumulate final audio segments per turn
    conversation_segments = []

    # Open a single WebSocket session
    async with websockets.connect(url, additional_headers=headers) as ws:
        # 1. Wait for session.created
        init_evt = await ws.recv()
        print("Received:", init_evt)  # {"type":"session.created", ...}

        # 2. Send session.update with interrupt_response enabled
        sess_update = {
            "type": "session.update",
            "session": {
                "voice": assistant_voice,         # e.g., "coral"
                "input_audio_format": "pcm16",    # 16-bit PCM @ 24 kHz
                "output_audio_format": "pcm16",   # assistant replies in PCM16
                "turn_detection": {
                    "type": "server_vad",        # server‐side VAD
                    "create_response": False,    # manual response.create per turn
                    "interrupt_response": True   # allow the user to interrupt
                }
            }
        }
        await ws.send(json.dumps(sess_update))
        upd_resp = await ws.recv()
        print("Received:", upd_resp)  # {"type":"session.updated", ...}

        # 3. Loop over each user audio file
        for idx, user_wav in enumerate(audio_files):
            print(f"\n--- TURN {idx+1} ---")

            # 3.1 Read & validate user audio (PCM16 @ 24 kHz mono)
            data, sr = sf.read(user_wav, dtype="int16")
            assert sr == 24000 and data.ndim == 1, "WAV must be 24 kHz mono PCM16"
            user_pcm = data.tobytes()
            b64_user_audio = base64.b64encode(user_pcm).decode("utf-8")

            # 3.2 Append user audio buffer
            append_msg = {
                "type": "input_audio_buffer.append",
                "audio": b64_user_audio
            }
            await ws.send(json.dumps(append_msg))

            # 3.3 Commit buffer as user turn
            commit_msg = { "type": "input_audio_buffer.commit" }
            await ws.send(json.dumps(commit_msg))

            # 3.4 Wait for commit & conversation.item.created
            while True:
                evt = await ws.recv()
                evt_obj = json.loads(evt)
                print("Received:", evt_obj)
                if evt_obj.get("type") == "input_audio_buffer.committed":
                    continue  # server ack of buffer commit
                if evt_obj.get("type") == "conversation.item.created":
                    break       # user turn registered

            # 3.5 **Always** request assistant response, regardless of prior interruptions
            resp_create = { "type": "response.create" }  # <— Moved here unconditionally
            await ws.send(json.dumps(resp_create))

            # 3.6 Collect assistant audio, with **delayed interruption on Turn 1 only**
            assistant_pcm = bytearray()
            interrupted = False

            # ◆ Initialize a counter to delay the interrupt by ~3 chunks (~0.12 s)
            delta_count = 0  #

            while True:
                resp_evt = await ws.recv()
                resp_obj = json.loads(resp_evt)

                # ◆ Count each audio delta chunk
                if resp_obj.get("type") == "response.audio.delta":
                    delta_count += 1

                # ◆ Only INTERRUPT on Turn 1 (idx == 0), after 3 deltas
                if idx == 0 and resp_obj.get("type") == "response.audio.delta" and delta_count >= 3:
                    assistant_pcm.extend(base64.b64decode(resp_obj["delta"]))
                    interrupted = True
                    print(f"🌟 Turn {idx+1} interrupted after {delta_count} deltas; starting Turn {idx+2}")
                    break

                # ◆ Normal accumulation of assistant audio deltas (when not interrupting)
                if resp_obj.get("type") == "response.audio.delta" and not interrupted:
                    chunk_b64 = resp_obj.get("delta", "")
                    if chunk_b64:
                        assistant_pcm.extend(base64.b64decode(chunk_b64))

                # ◆ If assistant finished (or was canceled), exit loop
                if resp_obj.get("type") in ["response.done", "response.canceled"]:
                    print("Received assistant end:", resp_obj)
                    break

            # 3.7 Write this assistant’s partial/full audio to a WAV for concatenation
            assistant_turn_wav = f"assistant_turn_{idx+1}.wav"
            if assistant_pcm:
                with wave.open(assistant_turn_wav, "wb") as wav_out:
                    wav_out.setnchannels(1)       # mono
                    wav_out.setsampwidth(2)       # 16 bits
                    wav_out.setframerate(24000)   # 24 kHz
                    wav_out.writeframes(bytes(assistant_pcm))
                print(f"✅ Saved assistant turn {idx+1} to {assistant_turn_wav}")
            else:
                print(f"⚠️ No assistant audio for turn {idx+1}, skipping segment.")

            # 3.8 Append segments: user → short pause → assistant (interrupted or complete)
            user_array, _ = sf.read(user_wav, dtype="int16")
            if assistant_pcm:
                assistant_array, _ = sf.read(assistant_turn_wav, dtype="int16")
            else:
                assistant_array = np.zeros(0, dtype="int16")

            pause_len = int(0.3 * 24000)  # 0.3 s silence = 7,200 samples
            pause = np.zeros(pause_len, dtype="int16")

            segment = np.concatenate((user_array, pause, assistant_array))
            conversation_segments.append(segment)

            # 3.9 If this turn was interrupted (only Turn 1), immediately proceed to next iteration
            if interrupted:
                continue

        # 4. Concatenate and write final_output
        if conversation_segments:
            final_audio = np.concatenate(conversation_segments)
            with wave.open(final_output, "wb") as wav_out:
                wav_out.setnchannels(1)
                wav_out.setsampwidth(2)
                wav_out.setframerate(24000)
                wav_out.writeframes(final_audio.tobytes())
            print(f"\n✅ Saved full conversation to {final_output}")
            display(Audio(final_output, rate=24000))
        else:
            print("⚠️ No conversation segments to concatenate.")

asyncio.run(run_multi_turn_conversation(audio_files, assistant_voice="coral", final_output="multi_turn_conversation.wav"))


Received: {"type":"session.created","event_id":"event_Be0jSvGqiWQQSFwo4GFTA","session":{"id":"sess_Be0jSjr2LY1F5xTYULsPh","object":"realtime.session","expires_at":1748877434,"input_audio_noise_reduction":null,"turn_detection":{"type":"server_vad","threshold":0.5,"prefix_padding_ms":300,"silence_duration_ms":200,"create_response":true,"interrupt_response":true},"input_audio_format":"pcm16","input_audio_transcription":null,"client_secret":null,"include":null,"model":"gpt-4o-realtime-preview-2024-10-01","modalities":["audio","text"],"instructions":"Your knowledge cutoff is 2023-10. You are a helpful, witty, and friendly AI. Act like a human, but remember that you aren't a human and that you can't do human things in the real world. Your voice and personality should be warm and engaging, with a lively and playful tone. If interacting in a non-English language, start by using the standard accent or dialect familiar to the user. Talk quickly. You should always call a function if you can. Do n

In [ ]:
import asyncio
import websockets
import json
import uuid
import base64
import wave
import soundfile as sf
import numpy as np
from IPython.display import Audio, display

# Step 0: Generate the single user-audio file (“How’s the weather...?”)
user_texts = ["Hows the weather looking like? in SF?"]
weather_ask = asyncio.run(generate_user_audio_inputs(user_texts))
# weather_ask == ["user_input_1.wav"] :contentReference[oaicite:3]{index=3}

# Stub function
def get_current_weather(city: str) -> str:
    return f"The current weather in {city} is 72°F, clear skies."

async def run_single_turn_conversation_with_real_function(
    user_wavs,
    assistant_wav="assistant_response.wav",
    conversation_wav="conversation.wav"
):
    """
    Streams one user WAV to OpenAI Realtime API, lets GPT-4o organically
    call get_current_weather, and then concatenates user + pause + assistant
    (spoken function result) into one WAV.
    """

    # 1. Connect to the Realtime WebSocket for GPT-4o Realtime
    url = "wss://api.openai.com/v1/realtime?model=gpt-4o-realtime-preview-2024-10-01"
    headers = {
        "Authorization": f"Bearer {API_KEY}",
        "OpenAI-Beta": "realtime=v1"
    }

    conversation_segments = []

    async with websockets.connect(url, additional_headers=headers) as ws:
        # 2. Wait for session.created acknowledgment
        init_evt = await ws.recv()
        print("Received:", init_evt)  # e.g., {"type":"session.created", ...} :contentReference[oaicite:4]{index=4}

        # 3. Send session.update with our function metadata
        sess_update = {
            "type": "session.update",
            "session": {
                "voice": "ash",
                "input_audio_format": "pcm16",
                "output_audio_format": "pcm16",
                "turn_detection": {
                    "type": "server_vad",
                    "create_response": False
                },
                "tools": [
                    {
                        "type": "function",
                        "name": "get_current_weather",
                        "description": "Returns current weather for a given city.",
                        "parameters": {
                            "type": "object",
                            "properties": {
                                "city": {
                                    "type": "string",
                                    "description": "Name of the city to get weather for"
                                }
                            },
                            "required": ["city"]
                        }
                    }
                ],
                "tool_choice": "auto"
            }
        }
        await ws.send(json.dumps(sess_update))
        upd_resp = await ws.recv()
        print("Received:", upd_resp)  # {"type":"session.updated", ...} :contentReference[oaicite:5]{index=5}

        # 4. Only one turn (turn_idx = 0)
        user_wav = user_wavs[0]
        print("\n--- TURN 1 ---")

        # 4.1 Read & encode user WAV (24 kHz mono PCM16)
        data, sr = sf.read(user_wav, dtype="int16")
        assert sr == 24000 and data.ndim == 1, "WAV must be 24 kHz mono PCM16"
        user_pcm = data.tobytes()
        b64_audio = base64.b64encode(user_pcm).decode("utf-8")

        # 4.2 Append user audio
        await ws.send(json.dumps({
            "type": "input_audio_buffer.append",
            "audio": b64_audio
        }))
        # :contentReference[oaicite:6]{index=6}

        # 4.3 Commit as a user turn
        await ws.send(json.dumps({
            "type": "input_audio_buffer.commit",
            "event_id": str(uuid.uuid4())
        }))
        # :contentReference[oaicite:7]{index=7}

        # 4.4 Wait for commit & conversation.item.created
        while True:
            evt = await ws.recv()
            evt_obj = json.loads(evt)
            print("Received:", evt_obj)
            if evt_obj.get("type") == "input_audio_buffer.committed":
                continue
            if evt_obj.get("type") == "conversation.item.created":
                break  # user turn is now registered :contentReference[oaicite:8]{index=8}

        # 4.5 Request the assistant’s response
        await ws.send(json.dumps({
            "type": "response.create",
            "event_id": str(uuid.uuid4())
        }))
        # :contentReference[oaicite:9]{index=9}

        # 4.6 Collect:
        #       • Listen for a `response.function_call` (the model’s request to call our function).
        #       • When seen, execute stub and send back the function result via `conversation.item.create`.
        #       • Immediately send a second `response.create` to stream the spoken function output.
        #       • Skip the first `response.done` (which only closes the function_call request),
        #         then collect audio deltas until the second `response.done`.
        collected_pcm = bytearray()
        function_call_id = None
        saw_first_done = False

        while True:
            resp_evt = await ws.recv()
            resp_obj = json.loads(resp_evt)

            # A) MODEL REQUESTS FUNCTION CALL
            if resp_obj.get("type") == "response.output_item":
                # This payload wraps the actual item; check for type=="function_call"
                item = resp_obj["item"]
                if item["type"] == "function_call":
                    function_call_id = item["call_id"]
                    func_name = item["name"]
                    func_args = json.loads(item["arguments"])
                    print(f"🌐 Assistant requested function '{func_name}' with args={func_args}")  # :contentReference[oaicite:10]{index=10}

                    # Execute the function (here, our stub)
                    if func_name == "get_current_weather":
                        city = func_args.get("city", "")
                        result_str = get_current_weather(city)

                        # 4.6b: Send back the function result
                        await ws.send(json.dumps({
                            "type": "conversation.item.create",
                            "item": {
                                "type": "function_call_output",
                                "call_id": function_call_id,
                                "output": result_str
                            }
                        }))
                        # :contentReference[oaicite:11]{index=11}

                        # 4.6c: Immediately request a second response so we get the spoken output
                        await ws.send(json.dumps({
                            "type": "response.create",
                            "event_id": str(uuid.uuid4())
                        }))
                        # :contentReference[oaicite:12]{index=12}
                    continue

            # B) COLLECT AUDIO DELTAS (before or after function_call)
            elif resp_obj.get("type") == "response.audio.delta":
                delta_b64 = resp_obj.get("delta", "")
                if delta_b64:
                    collected_pcm.extend(base64.b64decode(delta_b64))
                continue

            # C) HANDLE response.done
            elif resp_obj.get("type") == "response.done":
                # 1st response.done comes after model issues the function_call—
                # so if function_call_id is still None, keep waiting.
                if function_call_id is None:
                    # model ended its request for the function, but we haven't seen function_call yet
                    continue
                # If we’ve seen function_call but not yet seen a first done, mark and keep waiting.
                if not saw_first_done:
                    saw_first_done = True
                    # This first done corresponds to end of “function_call” request phase; keep listening
                    continue
                # If we arrive here, it is the second done (after model spoke the function result).
                print("Received assistant end:", resp_obj)  # :contentReference[oaicite:13]{index=13}
                break

            # D) IF canceled, bail out
            elif resp_obj.get("type") == "response.canceled":
                print("Response canceled:", resp_obj)
                break

        # 4.7 Write assistant WAV (PCM16 @ 24 kHz) from `collected_pcm`
        if collected_pcm:
            with wave.open(assistant_wav, "wb") as wav_out:
                wav_out.setnchannels(1)
                wav_out.setsampwidth(2)
                wav_out.setframerate(24000)
                wav_out.writeframes(bytes(collected_pcm))
            print(f"✅ Saved assistant audio to {assistant_wav}")  # :contentReference[oaicite:14]{index=14}
        else:
            print("⚠️ No assistant audio received.")
            return  # abort

        # 4.8 Concatenate user + 0.5s pause + assistant
        user_array, _ = sf.read(user_wav, dtype="int16")
        assistant_array, _ = sf.read(assistant_wav, dtype="int16")
        pause = np.zeros(int(0.5 * 24000), dtype="int16")
        segment = np.concatenate((user_array, pause, assistant_array))
        conversation_segments.append(segment)

        # 5. Write final conversation.wav
        if conversation_segments:
            final_audio = np.concatenate(conversation_segments)
            with wave.open(conversation_wav, "wb") as wav_out:
                wav_out.setnchannels(1)
                wav_out.setsampwidth(2)
                wav_out.setframerate(24000)
                wav_out.writeframes(final_audio.tobytes())
            print(f"\n✅ Saved full conversation to {conversation_wav}")
            display(Audio(conversation_wav, rate=24000))  # :contentReference[oaicite:15]{index=15}
        else:
            print("⚠️ No segments to concatenate.")

# Run it
asyncio.run(run_single_turn_conversation_with_real_function(
    user_wavs=weather_ask,
    assistant_wav="assistant_response.wav",
    conversation_wav="conversation.wav"
))


✅ Saved: user_input_1.wav
Received: {"type":"session.created","event_id":"event_Be0pmIYT9YbBI3fkPGilu","session":{"id":"sess_Be0pm4nfceOJAGuO7uNXD","object":"realtime.session","expires_at":1748877826,"input_audio_noise_reduction":null,"turn_detection":{"type":"server_vad","threshold":0.5,"prefix_padding_ms":300,"silence_duration_ms":200,"create_response":true,"interrupt_response":true},"input_audio_format":"pcm16","input_audio_transcription":null,"client_secret":null,"include":null,"model":"gpt-4o-realtime-preview-2024-10-01","modalities":["text","audio"],"instructions":"Your knowledge cutoff is 2023-10. You are a helpful, witty, and friendly AI. Act like a human, but remember that you aren't a human and that you can't do human things in the real world. Your voice and personality should be warm and engaging, with a lively and playful tone. If interacting in a non-English language, start by using the standard accent or dialect familiar to the user. Talk quickly. You should always call a

KeyboardInterrupt: 